In [3]:
import time
import json
import loguru
import random
import requests
import pymongo
from tqdm import tqdm
import sinaweibopy3
import webbrowser
from argparse import Namespace


logger = loguru.logger

headers = {
    'Referer': 'http:www.baidu.com',
    "Upgrade-Insecure-Requests": "1",
    "Connection": "keep-alive", 
    "Cache-Control": "max-age=0",
    'User-Agent': 'Mozilla/5.0 (Windows NT 10.0; WOW64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/65.0.3325.181 Safari/537.36',
    "Accept-Language": "zh-CN,zh;q=0.9,en;q=0.8,la;q=0.7,pl;q=0.6",
    "Accept": "text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8"
}


app1=Namespace(
    APP_KEY = '3197544314',
    APP_SECRET = '4413b78f879d08c0fd1afd69a9bc976c',
    REDIRECT_URL = 'https://api.weibo.com/oauth2/default.html'
)

app2=Namespace(
    APP_KEY = '3621364603',
    APP_SECRET = 'a8a1944bd8cca5624c30c371d7ce0e8b',
    REDIRECT_URL = 'https://api.weibo.com/oauth2/default.html'
)


In [4]:
# 访问授权有频次限制
try:
    client = sinaweibopy3.APIClient(app_key=app2.APP_KEY, app_secret=app2.APP_SECRET, redirect_uri=app2.REDIRECT_URL)
    url = client.get_authorize_url()
    logger.debug(url)
    webbrowser.open_new(url)
    
    result = client.request_access_token(input("please input code : "))  # Enter the CODE obtained in the authorized address
    logger.debug(result)
    
    # 过期时间 = 用户授权时间 + 授权有效期
    logger.info('expires in {}'.format(time.asctime( time.localtime(time.time()+result.expires_in))))
    access_token=result.access_token
    client.set_access_token(result.access_token, result.expires_in)

except ValueError:
    logger.debug('pyOauth2Error')

2019-04-25 22:59:34.333 | DEBUG    | __main__:<module>:5 - https://api.weibo.com/oauth2/authorize?response_type=code&client_id=3621364603&redirect_uri=https://api.weibo.com/oauth2/default.html
2019-04-25 22:59:38.825 | DEBUG    | __main__:<module>:9 - {'access_token': '2.009GpigHV3sExD568780f376gd9U3C', 'remind_in': '157679999', 'expires_in': 1713884377, 'uid': '7044218812', 'isRealName': 'true'}
2019-04-25 22:59:38.826 | INFO     | __main__:<module>:12 - expires in Wed Aug 16 13:59:15 2073


In [51]:
def comments_show(sid:int,count=50,page=1,filter_by_author=0):
    '''
    #根据微博id获取评论列表
    count:单页返回的记录条数，默认为50。
    page:默认为1
    filter_by_author:作者筛选类型，0：全部、1：我关注的人、2：陌生人，默认为0。
    ''' 
    params={}
    params['access_token']=access_token
    params['id']=sid
    params['count']=count
    params['page']=page
    params['filter_by_author']=filter_by_author
    url='https://api.weibo.com/2/comments/show.json'
    rsp=requests.get(url,params=params,headers=headers)
    logger.info(rsp.url)
    data=json.loads(rsp.text)
    return data

In [55]:
def parse_comments(data):
    '''
    #解析评论数据
    '''
    result=[]
    if 'error' in data.keys():
        logger.error(data)
    else:
        result=[]
        for s in data['comments']:
            dct={}
            dct['created_at'] = s['created_at']
            dct['_id'] = s['id']
            dct['uid'] = s['user']['id']
            dct['text'] = s['text']
            dct['pid'] = s['status']['id']
            result.append(dct)
    return result

In [45]:
pid = 4364996307427505 #4362359990330047,4364996307427505

for i in range(3):
    data = comments_show(sid=pid,count=20,page=i+1)
    print(parse_comments(data)[0])

2019-04-25 23:23:05.820 | DEBUG    | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4364996307427505&count=20&page=1&filter_by_author=0
2019-04-25 23:23:05.950 | DEBUG    | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4364996307427505&count=20&page=2&filter_by_author=0


{'created_at': 'Thu Apr 25 23:23:03 +0800 2019', 'cid': 4365105792212426, 'uid': 5958066543, 'text': '回复@邢邢邢朵朵:当你沉睡时！！！！真的好好看，我想起来就去刷！！', 'pid': 4364996307427505}
{'created_at': 'Thu Apr 25 23:19:15 +0800 2019', 'cid': 4365104835061935, 'uid': 6021229281, 'text': '回复@邢邢邢朵朵:当你沉睡时', 'pid': 4364996307427505}


2019-04-25 23:23:06.268 | DEBUG    | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4364996307427505&count=20&page=3&filter_by_author=0


{'created_at': 'Thu Apr 25 23:15:32 +0800 2019', 'cid': 4365103900210444, 'uid': 7017722257, 'text': '秀智好美啊', 'pid': 4364996307427505}


In [39]:
comments = parse_comments(data)

In [40]:
post_crawled=[]

In [63]:
def get_comments_from_mongodb():
	client = pymongo.MongoClient("mongodb://10.108.17.25:27017/")  # 10.108.17.25
	weibo_db = client["weibo"]
	post_table = weibo_db['post']
	comment_table = weibo_db['comment']
	posts = list(post_table.find())

	for post in tqdm(posts):
		pid = post['_id']
		logger.info("request comments for pid = {}".format(pid))
		time.sleep(random.randrange(5, 10))
        
		comments=[]
		for i in range(3):
			data = comments_show(sid=pid,count=20,page=i+1)
			data = parse_comments(data)
			comments.extend(data)
		
		if not comments:
			logger.debug('comments == []')
			continue
		# 保存数据
		for comment in comments:
			try:
				rst = comment_table.find_one({'_id': int(comment['_id'])})  # 必须是int
				if rst is not None:
					logger.info('cid = {} has saved!'.format(comment['_id']))
					continue
				rst = comment_table.insert_one(comment)
				if str(rst.inserted_id) == str(comment['_id']):
					post_crawled.append(comment['_id'])
					#logger.info('insert successful cid = {}'.format(comment['_id']))
				else:
					logger.info('insert comment faild cid={}'.format(comment['_id']))
			except Exception as e:
				logger.error('insert comment faild cid = {}'.format(comment['_id']))
				print(e)

In [ ]:
get_comments_from_mongodb()



  0%|          | 0/8478 [00:00<?, ?it/s]2019-04-25 23:31:35.918 | INFO     | __main__:get_comments_from_mongodb:10 - request comments for pid = 4362359990330047
2019-04-25 23:31:43.245 | INFO     | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4362359990330047&count=20&page=1&filter_by_author=0
2019-04-25 23:31:43.541 | INFO     | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4362359990330047&count=20&page=2&filter_by_author=0
2019-04-25 23:31:43.631 | INFO     | __main__:comments_show:16 - https://api.weibo.com/2/comments/show.json?access_token=2.009GpigHV3sExD568780f376gd9U3C&id=4362359990330047&count=20&page=3&filter_by_author=0
2019-04-25 23:31:43.632 | DEBUG    | __main__:get_comments_from_mongodb:20 - comments == []


  0%|          | 1/8478 [00:07<18:10:01,  7.72s/it]2019-04-25 23:31:43.634 | INFO     | __main__:get_comments_from_m